# [Largest Prime Factor](https://projecteuler.net/problem=3)

The [fundamental theorem of arithmetic](https://en.wikipedia.org/wiki/Fundamental_theorem_of_arithmetic) says that every integer greater than 1 has a unique prime factorization.

There are numerous factorization algorithms. Some of the easiest to implement are [trial division](https://en.wikipedia.org/wiki/Trial_division), [wheel factorization](https://en.wikipedia.org/wiki/Wheel_factorization) and [Pollard's rho algorithm](https://en.wikipedia.org/wiki/Pollard%27s_rho_algorithm).

In general, as an integer gets larger, [factoring it gets harder](https://en.wikipedia.org/wiki/Integer_factorization). We don't have any efficient algorithm for factoring in general, but somewhat strangely, we don't know for certain that no such algorithm exists.

Fortunately for us, this number is not too large for any of these algorithms, or for SageMath.

In [1]:
prime_factors(600851475143)

[71, 839, 1471, 6857]

If we wanted to implement our own factorization algorithm, though, Pollard's rho is relatively easy to implement and more efficient (on average) than trial division. It's also got some interesting math at its foundation, so let's take a look at it.

## Pollard's rho algorithm
Let $n=pq$ be a positive integer where $p$ and $q$ are non-trivial factors of $n$ (i.e. not 1 or $n$), and let $\{x_i\}$ be a sequence such that $x_0$ is some random initial value and
$$x_{i+1} = (x_i^2 - 1) \bmod{n}$$
Since the number of values this sequence can take on is finite, and each term is determined entirely by the previous term, it must ultimately become periodic, although there may be some initial terms before we reach a term that will repeat (refer to [this image](https://en.wikipedia.org/wiki/File:Pollard_rho_cycle.svg) for a visual aid - the fact this diagram looks like the Greek letter $\rho$ is where the algorithm gets its name).

How many terms will we see before the sequence repeats? If we assume the sequence is random, the [birthday paradox](https://en.wikipedia.org/wiki/Birthday_problem) implies that it will take an average of $O(\sqrt{n})$ iterations before it repeats (this is using [Big O notation](https://en.wikipedia.org/wiki/Big_O_notation)). Of course, the sequence is not truly random, but it *is* [pseudorandom](https://en.wikipedia.org/wiki/Pseudorandomness), and experimental results seem to corroborate this analysis despite the somewhat faulty assumption.

Now consider the related sequence $\{x_i \bmod p\}$. Obviously, we can't calculate this sequence directly since we don't know the value of $p$, but similarly to $\{x_i\}$, this sequence is eventually periodic, with an average of $O(\sqrt{p})$ iterations before a repetition. In other words, this sequence is expected to repeat earlier than $\{x_i\}$.

When $\{x_i \bmod p\}$ cycles, it implies that $x_j \equiv x_k \pmod{p}$ for some $j \neq k$. This implies that $p | (x_j - x_k)$. Since $p$ also divides $n$, this means that $\gcd(x_j - x_k, n)$ will be some multiple of $p$.

This all means that we simply need to iterate through terms in $\{x_i\}$ until we find $x_j$ and $x_k$ such that $\gcd(x_j - x_k, n)$ equals something other than 1. When it does, by definition this will be a factor of $n$. However, this factor may be $n$ itself, which is trivial. In this case the algorithm fails, but it can be attempted again with a different value for $x_0$.

To facilitate finding $x_j$ and $x_k$, [Floyd's cycle-finding algorithm](https://en.wikipedia.org/wiki/Cycle_detection) is used. Briefly, two variables are used to iterate through $\{x_i\}$ at different rates. Because of this, the two variables will never have the same index, but eventually $x_i \equiv x_j \pmod{p}$, which we will detect with the GCD.

In [2]:
from itertools import count

def factorization(n):
    x = randint(0, n-1)
    y = x
    k = 2
    for i in count(1):
        x = (x ** 2 - 1) % n
        d = gcd(y - x, n)
        
        assert d != n
        
        if d != 1:
            return d
        
        if i == k:
            y = x
            k *= 2

Note that this algorithm gives us a factor, but not necessarily a *prime* factor. However, we could just repeatedly apply the algorithm until we only have prime factors left. But how do we know when a factor is prime? We'll need a [primality test](https://en.wikipedia.org/wiki/Primality_test) like the Miller-Rabin algorithm - see [problem 7](https://projecteuler.net/problem=7) for a discussion of that algorithm.

## Relevant sequences
* Greatest prime factors: [A006530](https://oeis.org/A006530)